Food diveristy in select European cities
===
An aspiring data scientist's foray into theories of culture
---
----

### A. Gutmanas
#### Cambridge, 1 March 2020

-------

## Part 1
### Getting geolocation data

In [1]:
import pandas as pd
import requests
import folium
from shapely.geometry import shape, Point
import math
import json

### 1A: London
Surprisingly, London open data is not easily discoverable. Luckily, AirBnB offers a rich selection of data for major cities, including geospatial data of boroughs and neighbourhoods. The data is distributed under the CC0 license - i.e., public domain. I will use this source for London and later for Stockholm (1B). Full list is available from http://insideairbnb.com/get-the-data.html

In [2]:
# get London boroughs
airbnb_london_url = "http://data.insideairbnb.com/united-kingdom/england/london/2019-11-05/visualisations/neighbourhoods.geojson"
london_boroughs_geojson = requests.get(airbnb_london_url).json()

In [3]:
london_boroughs_geojson['features'][0]['properties']

{'neighbourhood': 'Kingston upon Thames', 'neighbourhood_group': None}

In [4]:
print(f"AirBnB shows {len(london_boroughs_geojson['features'])} boroughs in London")

AirBnB shows 33 boroughs in London


33 boroughs with multimillion population is not enough granularity to do a proper analysis of which restaurants are close to each other. I explored alternatives such as postal code areas, but they are not too robust. Some datasets are not free, others are incomplete, or come in different formats that would require some effort to understand and parse. Ultimately, I need a set of points, spread over the area I want to study. Hence, I will go by a "brute force" approach and will cover the 33 boroughs of Greater London in hexagons of 2km in cross-section. These hexagons approximate a circle with a 1km radius. 


To do this, I need values for how long a degree is in meters at different latitudes, which is available from http://www.csgnetwork.com/degreelenllavcalc.html

In [5]:
# length of 1 degree latitude (more or less invariable) (in m)
lat1deg = 111257.79456880149
# length of 1 degree longitude at 51.5 degrees latitude (in m)
lng1deg = 69440.48979357751

A few utility functions will be needed for each city

In [6]:
def get_polygons(geojson_obj, borough_key="neighbourhood"):
    # Create shapely "shapes" for each borough to later position the hexagons     
    polygons = []
    for borough in geojson_obj["features"]:
        polygons.append(
            {
                "Borough": borough["properties"][borough_key],
                "shape": shape(borough["geometry"])
            }
        )
    return polygons

In [7]:
london_polygons = get_polygons(london_boroughs_geojson)

In [8]:
def get_city_box(polygons):
    # find the bounding box for all of the boroughs   
    min_lng = min([x["shape"].bounds[0] for x in polygons])
    min_lat = min([x["shape"].bounds[1] for x in polygons])
    max_lng = max([x["shape"].bounds[2] for x in polygons])
    max_lat = max([x["shape"].bounds[3] for x in polygons])
    
    return min_lng, min_lat, max_lng, max_lat    

In [9]:
def get_centre(bounding_box):
    # get an approximate centre of the city to later use in centering maps
    min_lng, min_lat, max_lng, max_lat = bounding_box
    return 0.5*(max_lat + min_lat), 0.5*(max_lng + min_lng)

The function below will be re-used for other cities, so it makes sense to define it here once

In [10]:
def get_hexagons(polygons, lat1deg, lng1deg, size=2000):
    # Main function to calculate the centres for the hexagons overlaying the whole city
    min_lng, min_lat, max_lng, max_lat = get_city_box(polygons)
    
    delta1km_lat = size / lat1deg
    delta1km_lng = size / lng1deg
    print(f"1 km change in latitude is {delta1km_lat} degrees")
    print(f"1 km change in longitude is {delta1km_lng} degrees")
    
    # To iterate over hexagons, some secondary school trigonometry is needed 
    # I will need to define increments in degrees for latitude and longitude   
    # for longitude, the hexagonal tiles will form neat rows, touching via their edges, 
    # so my increment is actually delta * cos(30 deg)
    inc_lng = delta1km_lng*0.5*math.sqrt(3)
    # each row will be shifted by half a tile with respect to the one above it,
    # so the increment between rows is 3/4 of the delta defined above
    inc_lat = delta1km_lat*0.75

    # it is easier to iterate over integers, so calculate how many rows and how many tiles in each row
    max_tiles_lat = math.ceil((max_lat - min_lat)/inc_lat)
    max_tiles_lng = math.ceil((max_lng - min_lng)/inc_lng) + 1 
    # The +1 above is to account for shifted odd rows by half a tile
    
    tiles = {
        "Borough": [],
        "Latitude": [],
        "Longitude": []
    }

    for lat_index in range(max_tiles_lat):
        lat = min_lat + lat_index*inc_lat
        if lat_index % 2 == 0:
            shift_lng = 0 # even rows
        else:
            shift_lng = -0.5 # odd rows need to shift by half a tile
        for lng_index in range(max_tiles_lng):
            lng = min_lng + (shift_lng + lng_index)*inc_lng
            point = Point(lng, lat)
            for polygon in polygons:
                if polygon["shape"].contains(point):
                    tiles["Borough"].append(polygon["Borough"])
                    tiles["Latitude"].append(lat)
                    tiles["Longitude"].append(lng)
                    break
    return pd.DataFrame(tiles)


In [11]:
london_df = get_hexagons(london_polygons, lat1deg, lng1deg)
london_df.head()


1 km change in latitude is 0.01797626860887671 degrees
1 km change in longitude is 0.028801640166210035 degrees


Borough   Latitude  Longitude
0  Croydon  51.300242  -0.123759
1  Croydon  51.300242  -0.098816
2  Bromley  51.300242   0.050841
3  Bromley  51.300242   0.075784
4  Croydon  51.313724  -0.136231

In [12]:
london_df.shape

(606, 3)

In [13]:
centre_lat, centre_lng = get_centre(get_city_box(london_polygons))

In [14]:
london_map = folium.Map(
    location=[centre_lat, centre_lng], 
    zoom_start=10, 
    tiles='cartodbpositron'
)

for borough in london_boroughs_geojson["features"]:
    folium.GeoJson(
        borough,
        name='geojson'
    ).add_to(london_map)

for lat, lng in zip(london_df["Latitude"], london_df["Longitude"]):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=None,
        color='#d8b365',
        fill=True,
        fill_color='#d8b365',
        fill_opacity=0.3,
        parse_html=False
    ).add_to(london_map)  


london_map


-----
### 1B: Stockholm

Let's repeat the process for Stockholm.

In [15]:
airbnb_stockholm_url = "http://data.insideairbnb.com/sweden/stockholms-l%C3%A4n/stockholm/2019-11-28/visualisations/neighbourhoods.geojson"
stockholm_boroughs_geojson = requests.get(airbnb_stockholm_url).json()

In [16]:
stockholm_boroughs_geojson["features"][0]["properties"]

{'neighbourhood': 'Kungsholmens', 'neighbourhood_group': None}

In [17]:
print(f"AirBnB shows {len(stockholm_boroughs_geojson['features'])} boroughs in Stockholm")

AirBnB shows 14 boroughs in Stockholm


In [18]:
stockholm_polygons = get_polygons(stockholm_boroughs_geojson)

In [19]:
centre_lat, centre_lng = get_centre(get_city_box(stockholm_polygons))
print(f"Approximate latitude and longitude of city centre {centre_lat}, {centre_lng}")

Approximate latitude and longitude of city centre 59.3338485, 17.9803555


In [20]:
# length of 1 degree latitude (more or less invariable) (in m)
lat1deg = 111400.779107962
# length of 1 degree longitude at 59.3 degrees latitude (in m)
lng1deg = 56924.3640095373

In [21]:
stockholm_df = get_hexagons(stockholm_polygons, lat1deg, lng1deg)
stockholm_df.head()

1 km change in latitude is 0.017953195803610468 degrees
1 km change in longitude is 0.03513434071331765 degrees


Borough   Latitude  Longitude
0                 Farsta  59.241084  18.080178
1                 Farsta  59.241084  18.110605
2             Skarpnäcks  59.241084  18.141032
3             Skarpnäcks  59.241084  18.171460
4  Enskede-Årsta-Vantörs  59.254549  18.034537

In [22]:
stockholm_df.shape

(83, 3)

In [23]:
stockholm_map = folium.Map(
    location=[centre_lat, centre_lng], 
    zoom_start=11, 
    tiles='cartodbpositron'
)

for borough in stockholm_boroughs_geojson["features"]:
    folium.GeoJson(
        borough,
        name='geojson'
    ).add_to(stockholm_map)

for lat, lng in zip(stockholm_df["Latitude"], stockholm_df["Longitude"]):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=None,
        color='#d8b365',
        fill=True,
        fill_color='#d8b365',
        fill_opacity=0.3,
        parse_html=False
    ).add_to(stockholm_map)  


stockholm_map


Hmmm. This is an order of magnitude smaller than the number of hexagons in London. Obviously, Stockholm is a smaller city, but still - Greater London and just inner Stockholm do not compare. As the Auntie Wikipedia says, in 2005, Greater Stockholm metropolitan area is defined as the entire Stockholm county: https://sv.wikipedia.org/wiki/Storstockholm. So let's be consistent and redo the hexagons.

Luckily, someone has already done the job for me! https://www.thenmap.net/ offers not just an REST API, but even a python module to access their data in a really simple way. The package and data are distributed under a permissive MIT license.

In [24]:
!pip install thenmap

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/opt/local/bin/python -m pip install --upgrade pip' command.


In [25]:
from thenmap import Thenmap

In [26]:
thenmap_api = Thenmap()
se_municipalities = thenmap_api["se-7"].get_geodata(properties=["name", "geo_crs=wgs84"])
se_counties = thenmap_api["se-4"].get_geodata(properties=["name","geo_crs=wgs84"])

In [27]:
se_municipalities['features'][0]['properties']

{'id': '114', 'entities': [{'name': 'Upplands Väsby kommun'}]}

In [28]:
for county in se_counties['features']:
    print(county['properties'])

{'id': '25', 'entities': [{'name': 'Norrbottens län'}]}
{'id': '24', 'entities': [{'name': 'Västerbottens län'}]}
{'id': '23', 'entities': [{'name': 'Jämtlands län'}]}
{'id': '22', 'entities': [{'name': 'Västernorrlands län'}]}
{'id': '21', 'entities': [{'name': 'Gävleborgs län'}]}
{'id': '20', 'entities': [{'name': 'Dalarnas län'}]}
{'id': '19', 'entities': [{'name': 'Västmanlands län'}]}
{'id': '18', 'entities': [{'name': 'Örebro län'}]}
{'id': '17', 'entities': [{'name': 'Värmlands län'}]}
{'id': '14', 'entities': [{'name': 'Västra Götalands län'}]}
{'id': '13', 'entities': [{'name': 'Hallands län'}]}
{'id': '12', 'entities': [{'name': 'Skåne län'}]}
{'id': '10', 'entities': [{'name': 'Blekinge län'}]}
{'id': '9', 'entities': [{'name': 'Gotlands län'}]}
{'id': '8', 'entities': [{'name': 'Kalmar län'}]}
{'id': '7', 'entities': [{'name': 'Kronobergs län'}]}
{'id': '6', 'entities': [{'name': 'Jönköpings län'}]}
{'id': '5', 'entities': [{'name': 'Östergötlands län'}]}
{'id': '4', 'entit

Unfortunately, the data on municipalities does not come with info on which county the municipality belongs to. I will only keep municiplaities for the Greater Stockholm, which is equal to the entire Stockholm county (län), whose id is 1.

First, let's create the usual shapely "shape" for the Stockholm county. Then, iterate over all municipalities to see if they belong to it.

In [29]:
stockholm_county_geojson = None
for county in se_counties['features']:
    if county['properties']['id'] == '1':
        stockholm_county_geojson = county
        break

stockholm_county_polygon = shape(stockholm_county_geojson['geometry'])
        
stockholm_kommuner = {'features': []}
for kommun in se_municipalities['features']:
    point = shape(kommun['geometry']).representative_point()
    if stockholm_county_polygon.contains(point):
        stockholm_kommuner['features'].append(kommun)
    
    

In [30]:
stockholm_kommuner_polygons = get_polygons(stockholm_kommuner, borough_key='id')

In [31]:
centre_lat, centre_lng = get_centre(get_city_box(stockholm_polygons))
print(f"Approximate latitude and longitude of city centre {centre_lat}, {centre_lng}")

Approximate latitude and longitude of city centre 59.3338485, 17.9803555


In [32]:
# length of 1 degree latitude (more or less invariable) (in m)
lat1deg = 111400.779107962
# length of 1 degree longitude at 59.3 degrees latitude (in m)
lng1deg = 56924.3640095373

In [33]:
greater_stockholm_df = get_hexagons(stockholm_kommuner_polygons, lat1deg, lng1deg)
greater_stockholm_df.head()

1 km change in latitude is 0.017953195803610468 degrees
1 km change in longitude is 0.03513434071331765 degrees


Borough   Latitude  Longitude
0     192  58.815823  17.803104
1     192  58.815823  17.833531
2     192  58.829288  17.818317
3     192  58.829288  17.848745
4     192  58.842753  17.833531

In [34]:
greater_stockholm_df.shape

(2369, 3)

In [35]:
from pandas.io.json import json_normalize
stockholm_kommuner_df = json_normalize(stockholm_kommuner['features'])
stockholm_kommuner_df['name'] = [x[0]['name'][:-7].strip() for x in stockholm_kommuner_df['properties.entities']]
stockholm_kommuner_df['name'] = [x[:-1] if x[-1]=="s" else x for x in stockholm_kommuner_df['name']]
stockholm_kommuner_df.set_index("properties.id", inplace=True)
stockholm_kommuner_df.head()

type                  properties.entities geometry.type  \
properties.id                                                               
114            Feature  [{'name': 'Upplands Väsby kommun'}]       Polygon   
115            Feature      [{'name': 'Vallentuna kommun'}]       Polygon   
117            Feature      [{'name': 'Österåkers kommun'}]  MultiPolygon   
120            Feature          [{'name': 'Värmdö kommun'}]  MultiPolygon   
123            Feature        [{'name': 'Järfälla kommun'}]       Polygon   

                                            geometry.coordinates  \
properties.id                                                      
114            [[[17.927819, 59.499164], [17.837943, 59.47623...   
115            [[[18.231394, 59.507875], [18.143295, 59.49340...   
117            [[[[18.577278, 59.549338], [18.41661, 59.48417...   
120            [[[[18.476409, 59.290579], [18.547159, 59.2674...   
123            [[[17.803439, 59.460655], [17.806923, 59.50616...   

                         name  
properties.id                  
114            Upplands Väsby  
115                Vallentuna  
117                 Österåker  
120                    Värmdö  
123                  Järfälla

In [36]:
greater_stockholm_df = greater_stockholm_df.join(stockholm_kommuner_df[["name"]], on="Borough")
greater_stockholm_df.drop(labels="Borough", axis=1, inplace=True)
greater_stockholm_df.head()


Latitude  Longitude       name
0  58.815823  17.803104  Nynäshamn
1  58.815823  17.833531  Nynäshamn
2  58.829288  17.818317  Nynäshamn
3  58.829288  17.848745  Nynäshamn
4  58.842753  17.833531  Nynäshamn

In [37]:
greater_stockholm_df.columns = ['Latitude', 'Longitude', 'Borough']

In [38]:
greater_stockholm_map = folium.Map(
    location=[59.3, 17.9], 
    zoom_start=8.5, 
    tiles='cartodbpositron'
)


folium.GeoJson(
    stockholm_county_geojson,
    name='geojson'
).add_to(greater_stockholm_map)

for lat, lng in zip(greater_stockholm_df["Latitude"], greater_stockholm_df["Longitude"]):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=None,
        color='#d8b365',
        fill=True,
        fill_color='#d8b365',
        fill_opacity=0.3,
        parse_html=False
    ).add_to(greater_stockholm_map)  



greater_stockholm_map


Wow. That's a lot of hexagons. The borders of the municipalities are a bit rough, but it should be fine for subsequent analysis of restaurant categories. There is a lot of green space, so many of these hexagons will disappear.

In [39]:
greater_stockholm_df = get_hexagons(stockholm_polygons, lat1deg, lng1deg)
greater_stockholm_df.head()

1 km change in latitude is 0.017953195803610468 degrees
1 km change in longitude is 0.03513434071331765 degrees


Borough   Latitude  Longitude
0                 Farsta  59.241084  18.080178
1                 Farsta  59.241084  18.110605
2             Skarpnäcks  59.241084  18.141032
3             Skarpnäcks  59.241084  18.171460
4  Enskede-Årsta-Vantörs  59.254549  18.034537

### 1C: Paris
I could repeat the same process for Paris, but I will also explore the official data from the French Government and the City of Paris open data portals, which in addition to boroughs (arrondissements) https://www.data.gouv.fr/en/datasets/arrondissements-1/, also contains administrative naighbourhoods (quartiers administratifs) https://opendata.paris.fr/explore/dataset/quartier_paris/export/. These particular files are provided by the office of the Mayor of Paris under the ODbL license.

In [40]:
boroughs_url = "https://www.data.gouv.fr/en/datasets/r/4765fe48-35fd-4536-b029-4727380ce23c"
neighbourhoods_url = "https://opendata.paris.fr/explore/dataset/quartier_paris/download/?format=geojson&timezone=Europe/London&lang=fr"

In [41]:
paris_boroughs_geojson = requests.get(boroughs_url).json()

In [42]:
paris_boroughs_geojson["features"][0]["properties"]

{'n_sq_co': 750001537,
 'n_sq_ar': 750000001,
 'objectid': 1,
 'l_ar': '1er Ardt',
 'longueur': 6054.68086176,
 'surface': 1824612.86048666,
 'geom_x_y': [48.8625627018, 2.33644336205],
 'perimetre': 6054.93686218,
 'l_aroff': 'Louvre',
 'c_arinsee': 75101,
 'c_ar': 1}

In [43]:
print(f"There are {len(paris_boroughs_geojson['features'])} boroughs in Paris")

There are 20 boroughs in Paris


In [44]:
paris_neighbourhoods_geojson = requests.get(neighbourhoods_url).json()

In [45]:
paris_neighbourhoods_geojson["features"][0]["properties"]

{'n_sq_qu': 750000021,
 'n_sq_ar': 750000006,
 'geom_x_y': [48.8543844036, 2.34003537113],
 'c_qu': 21,
 'surface': 293360.5723113,
 'l_qu': 'Monnaie',
 'perimetre': 2391.1228183,
 'c_quinsee': 7510601,
 'c_ar': 6}

In [46]:
print(f"There are {len(paris_neighbourhoods_geojson['features'])} neighbourhoods in Paris")

There are 80 neighbourhoods in Paris


So it seems that these neighbourhoods are rather large units, and for the sake of consistency I will also apply the hexagional tiles for Paris. How apt, as France itself is sometimes call "Le Hexagon". Maybe "La"? My French is getting rusty...

In [47]:
paris_polygons = get_polygons(paris_boroughs_geojson, borough_key="l_aroff")

In [48]:
centre_lat, centre_lng = get_centre(get_city_box(paris_polygons))
print(f"Approximate latitude and longitude of city centre {centre_lat}, {centre_lng}")

Approximate latitude and longitude of city centre 48.85886928712212, 2.346919702796149


In [49]:
# length of 1 degree latitude (more or less invariable) (in m)
lat1deg = 111201.94511891318
# length of 1 degree longitude at 59.3 degrees latitude (in m)
lng1deg = 73755.91150422128

In [50]:
paris_df = get_hexagons(paris_polygons, lat1deg, lng1deg)
paris_df.head()

1 km change in latitude is 0.017985296910600898 degrees
1 km change in longitude is 0.02711647052027191 degrees


Borough   Latitude  Longitude
0  Observatoire  48.829066   2.306271
1  Observatoire  48.829066   2.329754
2      Gobelins  48.829066   2.353238
3      Gobelins  48.829066   2.376722
4       Reuilly  48.829066   2.400205

In [51]:
paris_df.shape

(41, 3)

In [52]:
paris_map = folium.Map(
    location=[centre_lat, centre_lng], 
    zoom_start=11, 
    tiles='cartodbpositron'
)

for borough in paris_boroughs_geojson["features"]:
    folium.GeoJson(
        borough,
        name='geojson'
    ).add_to(paris_map)

for lat, lng in zip(paris_df["Latitude"], paris_df["Longitude"]):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=None,
        color='#d8b365',
        fill=True,
        fill_color='#d8b365',
        fill_opacity=0.3,
        parse_html=False
    ).add_to(paris_map)  


paris_map


Hmmm. Here is the difficulty of going by strict administrative areas. The 20 boroughs of Paris are so much more compact than the 33 boroughs of London - only 40 hexagons, compared to London's >600. Even Inner Stockholm had more  than Paris. So that made me dig a bit more, and there is a concept of "Metropole du Grand Paris", or Greater Paris. Let's try.

In [53]:
metropole_url = "https://opendata.arcgis.com/datasets/4c41f3fc9d96418c829855041bff5970_0.geojson"
grand_paris_geojson = requests.get(metropole_url).json()

In [54]:
grand_paris_geojson["features"][0]["properties"]

{'OBJECTID': 1,
 'N_SQ_EPT': 920000001,
 'L_EPT_MGP': 'T4 Territoire Paris Ouest La Défense',
 'C_DEP': 92,
 'SHAPE_Length': 46967.580829822786,
 'SHAPE_Area': 59173746.46992489}

In [55]:
print(f"There are {len(grand_paris_geojson['features'])} areas in Greater Paris")

There are 12 areas in Greater Paris


In [56]:
grand_paris_polygons = get_polygons(grand_paris_geojson, borough_key="L_EPT_MGP")

In [57]:
centre_lat, centre_lng = get_centre(get_city_box(grand_paris_polygons))
print(f"Approximate latitude and longitude of city centre {centre_lat}, {centre_lng}")

Approximate latitude and longitude of city centre 48.82924238762515, 2.3807027446061952


In [58]:
grand_paris_df = get_hexagons(grand_paris_polygons, lat1deg, lng1deg)
grand_paris_df.head()

1 km change in latitude is 0.017985296910600898 degrees
1 km change in longitude is 0.02711647052027191 degrees


Borough   Latitude  Longitude
0  T12 Grand-Orly Val-de-Bièvre Seine-Amont   48.659641   2.368793
1  T12 Grand-Orly Val-de-Bièvre Seine-Amont   48.673130   2.357051
2  T12 Grand-Orly Val-de-Bièvre Seine-Amont   48.673130   2.380535
3  T12 Grand-Orly Val-de-Bièvre Seine-Amont   48.686619   2.345309
4  T12 Grand-Orly Val-de-Bièvre Seine-Amont   48.686619   2.368793

In [59]:
grand_paris_df.shape

(313, 3)

Now that's more like it - a much more comparable scale with London.

In [60]:
grand_paris_map = folium.Map(
    location=[centre_lat, centre_lng], 
    zoom_start=10, 
    tiles='cartodbpositron'
)

for borough in grand_paris_geojson["features"]:
    folium.GeoJson(
        borough,
        name='geojson'
    ).add_to(grand_paris_map)

for lat, lng in zip(grand_paris_df["Latitude"], grand_paris_df["Longitude"]):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=None,
        color='#d8b365',
        fill=True,
        fill_color='#d8b365',
        fill_opacity=0.3,
        parse_html=False
    ).add_to(grand_paris_map)  


grand_paris_map


### 1D: Vilnius
And finally, a smaller city in Eastern Europe. 


In the case of Vilnius, the only comprehensive dataset I came across includes municipalities and subdistricts (“seniūnijos”) for the entire country (Lithuania). These datasets were prepared by Julius Seporaitis (https://github.com/seporaitis) and made available on his GitHub account at https://github.com/seporaitis/lt-geojson. I have cloned this project and will use the downloaded files instead of accessing them directly.

In [61]:
with open("lt-geojson/geojson/municipalities.geojson") as f:
    lith_municipalities = json.load(f)

In [62]:
lith_municipalities['features'][0]['properties']

{'@id': 'relation/966362',
 'ISO3166-2': 'LT-59',
 'admin_level': '5',
 'boundary': 'administrative',
 'name': 'Visagino savivaldybė',
 'name:lt': 'Visagino savivaldybė',
 'name:pl': 'rejon wisagiński',
 'name:ru': 'Висагинское самоуправление',
 'type': 'boundary',
 'wikidata': 'Q2558824',
 'wikipedia': 'lt:Visagino savivaldybė'}

In [67]:
len(lith_municipalities["features"])

114

Let's select the Vilnius city and the Vilnius suburban municipalities

Note that some of the "features" define "relationships"

In [76]:
vilnius_geojson = {"features": []}
for municipality in lith_municipalities['features']:
    name = municipality['properties'].get('name',"")
    if ("Vilniaus" in name):
        vilnius_geojson["features"].append(municipality)
        

len(vilnius_geojson["features"])

2

In [82]:
vilnius_polygons = get_polygons(vilnius_geojson, borough_key="name")

In [83]:
centre_lat, centre_lng = get_centre(get_city_box(vilnius_polygons))
print(f"Approximate latitude and longitude of city centre {centre_lat}, {centre_lng}")

Approximate latitude and longitude of city centre 54.7550849, 25.307185150000002


In [84]:
# length of 1 degree latitude (more or less invariable) (in m)
lat1deg = 111319.79997066555
# length of 1 degree longitude at 59.3 degrees latitude (in m)
lng1deg = 64312.02534351407

In [85]:
vilnius_df = get_hexagons(vilnius_polygons, lat1deg, lng1deg)
vilnius_df.head()

1 km change in latitude is 0.017966255783131393 degrees
1 km change in longitude is 0.031098383067820798 degrees


Borough   Latitude  Longitude
0  Vilniaus rajono savivaldybė  54.476563  25.161533
1  Vilniaus rajono savivaldybė  54.476563  25.242329
2  Vilniaus rajono savivaldybė  54.476563  25.269261
3  Vilniaus rajono savivaldybė  54.476563  25.296193
4  Vilniaus rajono savivaldybė  54.476563  25.538581

In [86]:
vilnius_df.shape

(975, 3)

In [87]:
vilnius_map = folium.Map(
    location=[centre_lat, centre_lng], 
    zoom_start=9, 
    tiles='cartodbpositron'
)

for borough in vilnius_geojson["features"]:
    folium.GeoJson(
        borough,
        name='geojson'
    ).add_to(vilnius_map)

for lat, lng in zip(vilnius_df["Latitude"], vilnius_df["Longitude"]):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=None,
        color='#d8b365',
        fill=True,
        fill_color='#d8b365',
        fill_opacity=0.3,
        parse_html=False
    ).add_to(vilnius_map)  


vilnius_map


## End of Part 1 (Geodata)
------

## Part 2:
### Getting Foursquare API data for each hexagon in the four metropolitan areas